In [41]:
import pandas as pd
import folium, copy, queue
import numpy as np
import networkx as nx
from haversine import haversine

In [42]:
food = pd.read_csv('jeju_food.csv', encoding='cp949')
exfood = food.iloc[:10000]
exfood.columns

Index(['사업장명', '업종구분대분류', '업종구분소분류', '인허가일자', '인허가취소일자', '영업상태명', '상세영업상태명',
       '폐업일자', '휴업시작일자', '휴업종료일자', '재개업일자', '소재지면적', '소재지전체주소', '도로명전체주소',
       '도로명우편번호', '데이터갱신일자'],
      dtype='object')

In [43]:
data = pd.read_csv('jeju_market.csv')
df_rest = data[data['상권업종대분류명'] == '음식']
df_rest = df_rest[:30]
df_rest.head()

Unnamed: 0       상호명 상권업종대분류명 상권업종중분류명   상권업종소분류명      표준산업분류명      시도명  \
0           2  아빠가닭튀기는집       음식     유흥주점      호프/맥주       기타 주점업  제주특별자치도   
1           5    숙성1퍼센트       음식       한식  한식/백반/한정식      한식 음식점업  제주특별자치도   
2           7     해녀촌식당       음식       한식  한식/백반/한정식      한식 음식점업  제주특별자치도   
3           8     죠스떡볶이       음식       분식      떡볶이전문  분식 및 김밥 전문점  제주특별자치도   
4          11     가르텐비어       음식     유흥주점      호프/맥주       기타 주점업  제주특별자치도   

   시군구명 행정동명 법정동명       행정동코드       법정동코드                        지번주소  \
0   제주시  한림읍  한림읍  5011025000  5011025024  제주특별자치도 제주시 한림읍 한림리 1199-3   
1   제주시  노형동  노형동  5011066000  5011012200      제주특별자치도 제주시 노형동 3785-3   
2  서귀포시  대정읍  대정읍  5013025000  5013025026  제주특별자치도 서귀포시 대정읍 가파리 70-13   
3   제주시  건입동  건입동  5011059000  5011010700        제주특별자치도 제주시 건입동 1442   
4   제주시  노형동  노형동  5011066000  5011012200      제주특별자치도 제주시 노형동 1054-3   

                   도로명주소    신우편번호   longitude   latitude  
0  제주특별자치도 제주시 한림읍 한림중앙로  63032.0  126.264860  33.412363  
1      제주특별자치도 제주시 노형10길  63083.0  126.479894  33.483335  
2   제주특별자치도 서귀포시 대정읍 가파로  63514.0  126.274126  33.166521  
3        제주특별자치도 제주시 임항로  63276.0  126.526797  33.516737  
4     제주특별자치도 제주시 월랑로10길  63097.0  126.476631  33.489020

In [44]:
df_rest = df_rest[['상호명', 'latitude', 'longitude']]
list_rest = [1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1]
list_post = [34, 200, 31, 3, 42, 543, 23, 11, 2, 3, 34, 200, 31, 3, 42, 543, 23, 11, 2, 3, 34, 200, 31, 3, 42, 543, 23, 11, 2, 3]

df_rest['is_rest'] = list_rest
df_rest['post_num'] = list_post

df_rest

상호명   latitude   longitude  is_rest  post_num
0    아빠가닭튀기는집  33.412363  126.264860        1        34
1      숙성1퍼센트  33.483335  126.479894        1       200
2       해녀촌식당  33.166521  126.274126        1        31
3       죠스떡볶이  33.516737  126.526797        1         3
4       가르텐비어  33.489020  126.476631        1        42
5       어머니몸국  33.537381  126.638489        1       543
6          나무  33.456186  126.710438        0        23
7       우도회초밥  33.508147  126.943877        1        11
8          월계  33.471712  126.573797        0         2
9       해맞이동산  33.398293  126.787215        1         3
10         진산  33.513075  126.541906        0        34
11         웅담  33.414713  126.261416        0       200
12    한라카페테리아  33.456081  126.556897        0        31
13         별밤  33.487281  126.478243        0         3
14       에덴분식  33.248249  126.564271        1        42
15      장독대찻집  33.487651  126.492956        1       543
16     한거리푸줏간  33.555406  126.794435        1        23
17     영산강가마솥  33.484283  126.543830        1        11
18       대성식당  33.544283  126.657955        1         2
19       세흥장식  33.513754  126.536847        0         3
20   대학로고전떡볶이  33.498178  126.530275        1        34
21      갯것이식당  33.503571  126.537233        1       200
22  세인트포클럽하우스  33.520536  126.738665        1        31
23      엉덩물물회  33.490966  126.494964        1         3
24       성화분식  33.512654  126.511077        1        42
25      오래해장국  33.504071  126.466735        1       543
26         억수  33.521110  126.566851        0        23
27         유달  33.262212  126.620591        0        11
28      영아네맛집  33.523121  126.856339        1         2
29     레이크휴게소  33.371402  126.379968        1         3

In [45]:
def calDist(graph, curnode): #curnode는 노드 이름
    disDict = {}
    shortest_paths = nx.single_source_dijkstra_path_length(graph, source=curnode, weight='weight') ## cutoff는 curPos로부터최대 거리(이이상은 안찾음)
    for node, distance in shortest_paths.items():
        if node < 10000 and distance>0: ##node들은 4050000000이상임 음식점은 그것보다 작게 설정
            disDict[node] = distance 

    # print(len(disDict))
    return disDict


In [46]:
nodes = pd.read_csv('Jeju_nodes.csv')
links = pd.read_csv('Jeju_links.csv')

nodes = nodes[['Id','NODE_NAME','latitude','longitude']]
links = links[['Source','Target','LENGTH']]
source_in = links['Source'].apply(lambda x : x in list(nodes['Id'])) # check Sources are in jeju_id
target_in = links['Target'].apply(lambda x : x in list(nodes['Id'])) # check Targets are in jeju_id
# source_in and target_in are boolean type pandas.Series which contains True or False
Jeju_links = links[source_in & target_in] # contain if both target and source are contained in jeju_id
G = nx.Graph()

for idx,row in nodes.iterrows():
    G.add_node(row['Id'],Label=row['NODE_NAME'],latitude=row['latitude'], longitude=row['longitude'])

for idx,row in Jeju_links.iterrows():    
    G.add_edge(row['Source'],row['Target'],weight = row['LENGTH'])

print(f"Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")


Nodes: 4218, Edges: 6017


*ADDING LINK(너무 긴 링크의 경우 잘라서 노드를 추가하기)

In [47]:
# Maximum length for a single link (adjust as needed)
"""
max_length = 500  # 예시로 500으로 설정

new_nodes_data = []  # 새로 생성된 노드 데이터를 저장할 리스트
new_links_data = []  # 새로 생성된 링크 데이터를 저장할 리스트

for idx, row in Jeju_links.iterrows():
    source_node = row['Source']
    target_node = row['Target']
    length = row['LENGTH']

    if length > max_length:
        # Calculate the number of intermediate nodes required
        num_intermediate_nodes = int(length / max_length)

        # Calculate the coordinates of the intermediate nodes
        source_lat, source_lon = nodes[nodes['Id'] == source_node][['latitude', 'longitude']].values[0]
        target_lat, target_lon = nodes[nodes['Id'] == target_node][['latitude', 'longitude']].values[0]

        for i in range(1, num_intermediate_nodes + 1):
            fraction = i / (num_intermediate_nodes + 1)
            lat = source_lat + fraction * (target_lat - source_lat)
            lon = source_lon + fraction * (target_lon - source_lon)
            node_id = f"intermediate_{idx}_{i}"  # Unique node id for intermediate node

            new_nodes_data.append([node_id, f"Intermediate {i}", lat, lon])
            new_links_data.append([node_id, target_node, max_length])

            # Update target_node for the next iteration
            target_node = node_id

# Add intermediate nodes and links to the dataframes
new_nodes_df = pd.DataFrame(new_nodes_data, columns=['Id', 'NODE_NAME', 'latitude', 'longitude'])
new_links_df = pd.DataFrame(new_links_data, columns=['Source', 'Target', 'LENGTH'])

# Concatenate the new data with the existing data
nodes = pd.concat([nodes, new_nodes_df], ignore_index=True)
Jeju_links = pd.concat([Jeju_links, new_links_df], ignore_index=True)
"""

'\nmax_length = 500  # 예시로 500으로 설정\n\nnew_nodes_data = []  # 새로 생성된 노드 데이터를 저장할 리스트\nnew_links_data = []  # 새로 생성된 링크 데이터를 저장할 리스트\n\nfor idx, row in Jeju_links.iterrows():\n    source_node = row[\'Source\']\n    target_node = row[\'Target\']\n    length = row[\'LENGTH\']\n\n    if length > max_length:\n        # Calculate the number of intermediate nodes required\n        num_intermediate_nodes = int(length / max_length)\n\n        # Calculate the coordinates of the intermediate nodes\n        source_lat, source_lon = nodes[nodes[\'Id\'] == source_node][[\'latitude\', \'longitude\']].values[0]\n        target_lat, target_lon = nodes[nodes[\'Id\'] == target_node][[\'latitude\', \'longitude\']].values[0]\n\n        for i in range(1, num_intermediate_nodes + 1):\n            fraction = i / (num_intermediate_nodes + 1)\n            lat = source_lat + fraction * (target_lat - source_lat)\n            lon = source_lon + fraction * (target_lon - source_lon)\n            node_id = f"intermed

데이터에 새로 노드들 추가하기

In [48]:
def connectRes(graph, df): # df는 idx, latitude, longitude가 있어야함
    nodes_latitude = nx.get_node_attributes(graph, 'latitude')
    nodes_longitude = nx.get_node_attributes(graph, 'longitude')
    for idx, row in df.iterrows():
        distances ={}
        for keyLong, valLat in nodes_latitude.items():
            nodesPos = (valLat, nodes_longitude[keyLong])
            curPos = (row['latitude'], row['longitude'])
            distances[keyLong] = haversine(nodesPos, curPos, unit='km')
        nearest_node = min(distances, key=distances.get)
        graph.add_node(idx, Label=row['상호명'], latitude=row['latitude'], longitude=row['longitude']) ##노드이름은 4050000000이하로 설정
        graph.add_edge(nearest_node, idx, weight=distances[nearest_node]) 
    return graph

G = connectRes(G, df_rest)
print(f"Data: {len(df_rest)}, Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")

Data: 30, Nodes: 4248, Edges: 6047


In [49]:
G[0]

AtlasView({4050134000: {'weight': 0.2430085827361106}})

In [50]:
print(calDist(G, 1))


{13: 612.8958602767785, 4: 838.7372836086237, 15: 1766.5624878478545, 23: 2003.1963092853464, 25: 3156.622597597204, 24: 5157.7805542934075, 20: 5919.84491250489, 21: 6312.5460525089675, 3: 6377.954854330404, 17: 6394.205111060184, 19: 6713.588317654041, 10: 7387.151502490586, 12: 8457.179679103856, 26: 9836.551397402352, 8: 10339.005365377636, 5: 17089.09859055799, 29: 17254.901790907246, 18: 18975.332983427033, 6: 24150.54136842636, 0: 24595.911856917235, 11: 24803.251118258195, 22: 28999.23486743101, 16: 32216.36982482893, 9: 33532.495631307975, 28: 38800.411385415064, 27: 39361.3509118001, 2: 39471.25279793145, 14: 40832.147176074395, 7: 45059.04852830987}


FOLIUM

In [51]:
std_point = tuple(nodes.head(4000)[['latitude','longitude']].iloc[3000]) # example of why we should add nodes

map_osm = folium.Map(location=std_point, zoom_start=12) 

# 도로망 표시
kw = {'opacity': 0.5, 'weight': 2}
for edge in G.edges(data=True):
    source, target, attributes = edge

    # Check if the source and target nodes exist in the graph
    if source in G.nodes and target in G.nodes:
        start = tuple([G.nodes[source]['latitude'], G.nodes[source]['longitude']])
        end = tuple([G.nodes[target]['latitude'], G.nodes[target]['longitude']])

        folium.PolyLine(
            locations=[start, end],
            color='blue',
            line_cap='round',
            **kw,
        ).add_to(map_osm)
    else:
        print(source, target)


# 식당 표시
for ix, row in df_rest.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=500, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='red',
        fill=True,  
    ).add_to(map_osm)

# node 표시
for ix, row in nodes.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=10, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='black',
        fill=True, 
    ).add_to(map_osm)

map_osm.add_child(folium.LatLngPopup())

In [95]:
def navigation(graph, curr_node, visited_node, dist, df, min_lst):
    if len(visited_node) > 4:
        min_lst.append({'visited_node': visited_node, 'dist': dist})
        return
    
    lst = calDist(graph, curr_node)

    for key, value in lst.items():
        node = df.loc[key]
        lst[key] = value / (np.log(node['post_num']  + 1))

        if node['is_rest'] == df['is_rest'].loc[curr_node]:
            lst[key] = 100000000000
    
    min_item = min(lst, key=lst.get)
    # print(min_item)

    updated_dist = 0

    for key, value in lst.items():
        if value < lst[min_item] * 100 and key not in visited_node:
            tmp = copy.deepcopy(visited_node)
            tmp.append(key)
            updated_dist = dist + value
            result = navigation(graph, key, tmp, updated_dist, df, min_lst)
            if result:
                return result

        # print([key, value])

In [53]:
def mapping(graph, df, node_list):
    map_osm_2 = folium.Map(location=[33.36364, 126.5639], zoom_start=10.5) 

    # 식당 표시
    for ix, row in df.iterrows():
        location = (row['latitude'], row['longitude']) 
        folium.Circle(
            location=location,
            radius=500, 
            color='white',
            weight=1,
            fill_opacity=0.6,
            opacity=1,
            fill_color='red',
            fill=True,  
        ).add_to(map_osm_2)

    for node_id in node_list:
        node = df.loc[node_id]
        location = (node['latitude'], node['longitude'])

        tooltip_text = f"출발지" if node_list.index(node_id) == 0 else f"{node_list.index(node_id)} 번째 장소<br>{node['상호명']}"
        marker_color = 'red' if node_list.index(node_id) == 0 else 'blue'

        folium.Marker(location, 
            icon=folium.Icon(color=marker_color),
            tooltip=folium.Tooltip(text=tooltip_text)).add_to(map_osm_2)


    # 노드 간의 경로를 Folium 지도에 추가
    for i in range(len(node_list)-1):
        start_node = node_list[i]
        end_node = node_list[i+1]
        path = nx.shortest_path(graph, source=start_node, target=end_node)

        print(path)
        # 경로의 좌표를 리스트로 변환
        path_coordinates = [(graph.nodes[node]['latitude'], graph.nodes[node]['longitude']) for node in path]
            
        # 경로를 선으로 추가
        folium.PolyLine(locations=path_coordinates, color='blue', weight=3).add_to(map_osm_2)

    return map_osm_2

In [89]:
def find_path(graph, src):
    modified_graph = copy.deepcopy(graph)
    data = {
        '상호명': ['src'],
        'latitude': [src[0]],
        'longitude': [src[1]]
    }
    df = pd.DataFrame(data)
    df = df.set_index(pd.Index([9999]))
    connectRes(modified_graph, df=df)

    visited_node = [9999]
    dist = 0

    df_added_src = copy.deepcopy(df_rest)
    new_row = pd.DataFrame({'상호명': ['src'], 'latitude': [src[0]], 'longitude': [src[1]]}, index=[9999])
    df_added_src = pd.concat([df_added_src, new_row])

    min_lst = []
    navigation(modified_graph, 9999, visited_node, dist, df_added_src, min_lst)

    print(f"length of min_lst = {len(min_lst)}")

    min_dist_entry = min(min_lst, key=lambda x: x['dist'])

    return mapping(modified_graph, df_added_src, min_dist_entry['visited_node'])

In [96]:
src = [33.39214, 126.4939]
navigated_map = find_path(G, src)

navigated_map

length of min_lst = 51279
[9999, 4050015900, 4050015800.0, 4050000201.0, 4050000502.0, 4050000500.0, 4050000503.0, 4050000900.0, 4050001100.0, 4050001101.0, 4050001102.0, 4050002501.0, 4050016400.0, 4050002502.0, 4050073800.0, 4050073802.0, 4050003500.0, 4050004101.0, 4050004100.0, 4050004400.0, 4050004600.0, 4050005000.0, 4050005002.0, 4050085000, 1]
[1, 4050085000, 4050084900.0, 4050005400.0, 4050005401.0, 4050006000.0, 4050006300.0, 4050033100.0, 4050034000, 13]
[13, 4050034000, 4050035900.0, 4050036800.0, 4050040100.0, 4050042300.0, 4050010100.0, 4050208601.0, 4050208701.0, 4050208801.0, 4050208901.0, 4050209201.0, 4050209001.0, 4050049800.0, 4050011501.0, 4050011700.0, 4050012400.0, 4050052900.0, 4050055600.0, 4050055400.0, 4050055000.0, 4050054700.0, 4050054701.0, 4050055500.0, 4050012900.0, 4050056500.0, 4050012700.0, 4050012801.0, 4050012800, 21]
[21, 4050012800, 4050013400.0, 4050013800.0, 4050062100.0, 4050062900, 10]
